ਇਸ ਨੋਟਬੁੱਕ ਵਿੱਚ, ਅਸੀਂ ਦਿਖਾਉਂਦੇ ਹਾਂ ਕਿ ਕਿਵੇਂ:

- 2D ਟਾਈਮ ਸੀਰੀਜ਼ ਡਾਟਾ ਨੂੰ SVM ਰਿਗ੍ਰੈਸਰ ਮਾਡਲ ਦੀ ਟ੍ਰੇਨਿੰਗ ਲਈ ਤਿਆਰ ਕਰਨਾ ਹੈ
- RBF ਕਰਨਲ ਦੀ ਵਰਤੋਂ ਕਰਕੇ SVR ਨੂੰ ਲਾਗੂ ਕਰਨਾ
- ਮਾਡਲ ਦਾ ਮੁਲਾਂਕਨ ਪਲਾਟਸ ਅਤੇ MAPE ਦੀ ਵਰਤੋਂ ਕਰਕੇ


## ਮੋਡੀਊਲਾਂ ਨੂੰ ਆਯਾਤ ਕਰਨਾ


In [1]:
import sys
sys.path.append('../../')

In [2]:
import os
import warnings
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import datetime as dt
import math

from sklearn.svm import SVR
from sklearn.preprocessing import MinMaxScaler
from common.utils import load_data, mape

### ਡਾਟਾ ਲੋਡ ਕਰੋ


In [3]:
energy = load_data('../../data')[['load']]
energy.head(5)

load
2012-01-01 00:00:00  2698.0
2012-01-01 01:00:00  2558.0
2012-01-01 02:00:00  2444.0
2012-01-01 03:00:00  2402.0
2012-01-01 04:00:00  2403.0

In [ ]:
energy.plot(y='load', subplots=True, figsize=(15, 8), fontsize=12)
plt.xlabel('timestamp', fontsize=12)
plt.ylabel('load', fontsize=12)
plt.show()

In [ ]:
train_start_dt = '2014-11-01 00:00:00'
test_start_dt = '2014-12-30 00:00:00'

In [ ]:
energy[(energy.index < test_start_dt) & (energy.index >= train_start_dt)][['load']].rename(columns={'load':'train'}) \
    .join(energy[test_start_dt:][['load']].rename(columns={'load':'test'}), how='outer') \
    .plot(y=['train', 'test'], figsize=(15, 8), fontsize=12)
plt.xlabel('timestamp', fontsize=12)
plt.ylabel('load', fontsize=12)
plt.show()

ਹੁਣ, ਤੁਹਾਨੂੰ ਆਪਣੇ ਡਾਟਾ ਨੂੰ ਫਿਲਟਰ ਕਰਨ ਅਤੇ ਸਕੇਲ ਕਰਨ ਦੁਆਰਾ ਟ੍ਰੇਨਿੰਗ ਲਈ ਤਿਆਰ ਕਰਨਾ ਚਾਹੀਦਾ ਹੈ।


In [ ]:
train = energy.copy()[(energy.index >= train_start_dt) & (energy.index < test_start_dt)][['load']]
test = energy.copy()[energy.index >= test_start_dt][['load']]

print('Training data shape: ', train.shape)
print('Test data shape: ', test.shape)

ਡਾਟਾ ਨੂੰ (0, 1) ਦੀ ਰੇਂਜ ਵਿੱਚ ਲਿਆਓ।


In [ ]:
scaler = MinMaxScaler()
train['load'] = scaler.fit_transform(train)
train.head(5)

In [ ]:
test['load'] = scaler.transform(test)
test.head(5)

ਸਾਡੇ SVR ਲਈ, ਅਸੀਂ ਇਨਪੁਟ ਡਾਟਾ ਨੂੰ `[batch, timesteps]` ਦੇ ਰੂਪ ਵਿੱਚ ਬਦਲਦੇ ਹਾਂ। ਇਸ ਲਈ, ਅਸੀਂ ਮੌਜੂਦਾ `train_data` ਅਤੇ `test_data` ਨੂੰ ਇਸ ਤਰ੍ਹਾਂ ਰੀਸ਼ੇਪ ਕਰਦੇ ਹਾਂ ਕਿ ਇੱਕ ਨਵਾਂ ਡਾਇਮੈਂਸ਼ਨ ਹੋਵੇ ਜੋ ਟਾਈਮਸਟੈਪਸ ਨੂੰ ਦਰਸਾਉਂਦਾ ਹੈ। ਸਾਡੇ ਉਦਾਹਰਨ ਲਈ, ਅਸੀਂ `timesteps = 5` ਲੈਂਦੇ ਹਾਂ। ਇਸ ਲਈ, ਮਾਡਲ ਲਈ ਇਨਪੁਟ ਪਹਿਲੇ 4 ਟਾਈਮਸਟੈਪਸ ਲਈ ਡਾਟਾ ਹੈ, ਅਤੇ ਆਉਟਪੁਟ 5ਵੇਂ ਟਾਈਮਸਟੈਪ ਲਈ ਡਾਟਾ ਹੋਵੇਗਾ।


In [ ]:
# Converting to numpy arrays

train_data = train.values
test_data = test.values

In [ ]:
# Selecting the timesteps

timesteps=None

In [ ]:
# Converting data to 2D tensor

train_data_timesteps=None

In [ ]:
# Converting test data to 2D tensor

test_data_timesteps=None

In [ ]:
x_train, y_train = None
x_test, y_test = None

print(x_train.shape, y_train.shape)
print(x_test.shape, y_test.shape)

In [ ]:
# Create model using RBF kernel

model = None

In [ ]:
# Fit model on training data

### ਮਾਡਲ ਅਨੁਮਾਨ ਲਗਾਓ


In [ ]:
# Making predictions

y_train_pred = None
y_test_pred = None

In [ ]:
# Scaling the predictions

y_train_pred = scaler.inverse_transform(y_train_pred)
y_test_pred = scaler.inverse_transform(y_test_pred)

In [ ]:
# Scaling the original values

y_train = scaler.inverse_transform(y_train)
y_test = scaler.inverse_transform(y_test)

In [ ]:
# Extract the timesteps for x-axis

train_timestamps = None
test_timestamps = None

In [ ]:
plt.figure(figsize=(25,6))
# plot original output
# plot predicted output
plt.legend(['Actual','Predicted'])
plt.xlabel('Timestamp')
plt.title("Training data prediction")
plt.show()

In [ ]:
print('MAPE for training data: ', mape(y_train_pred, y_train)*100, '%')

In [ ]:
plt.figure(figsize=(10,3))
# plot original output
# plot predicted output
plt.legend(['Actual','Predicted'])
plt.xlabel('Timestamp')
plt.show()

In [ ]:
print('MAPE for testing data: ', mape(y_test_pred, y_test)*100, '%')

## ਪੂਰਾ ਡੇਟਾਸੈਟ ਅਨੁਮਾਨ


In [ ]:
# Extracting load values as numpy array
data = None

# Scaling
data = None

# Transforming to 2D tensor as per model input requirement
data_timesteps=None

# Selecting inputs and outputs from data
X, Y = None, None

In [ ]:
# Make model predictions

# Inverse scale and reshape
Y_pred = None
Y = None

In [ ]:
plt.figure(figsize=(30,8))
# plot original output
# plot predicted output
plt.legend(['Actual','Predicted'])
plt.xlabel('Timestamp')
plt.show()

In [ ]:
print('MAPE: ', mape(Y_pred, Y)*100, '%')


---

**ਅਸਵੀਕਾਰਨਾ**:  
ਇਹ ਦਸਤਾਵੇਜ਼ AI ਅਨੁਵਾਦ ਸੇਵਾ [Co-op Translator](https://github.com/Azure/co-op-translator) ਦੀ ਵਰਤੋਂ ਕਰਕੇ ਅਨੁਵਾਦ ਕੀਤਾ ਗਿਆ ਹੈ। ਹਾਲਾਂਕਿ ਅਸੀਂ ਸਹੀਅਤਾ ਲਈ ਯਤਨਸ਼ੀਲ ਹਾਂ, ਕਿਰਪਾ ਕਰਕੇ ਧਿਆਨ ਦਿਓ ਕਿ ਸਵੈਚਾਲਿਤ ਅਨੁਵਾਦਾਂ ਵਿੱਚ ਗਲਤੀਆਂ ਜਾਂ ਅਸੁਚਨਾਵਾਂ ਹੋ ਸਕਦੀਆਂ ਹਨ। ਮੂਲ ਦਸਤਾਵੇਜ਼ ਨੂੰ ਇਸਦੀ ਮੂਲ ਭਾਸ਼ਾ ਵਿੱਚ ਅਧਿਕਾਰਤ ਸਰੋਤ ਮੰਨਿਆ ਜਾਣਾ ਚਾਹੀਦਾ ਹੈ। ਮਹੱਤਵਪੂਰਨ ਜਾਣਕਾਰੀ ਲਈ, ਪੇਸ਼ੇਵਰ ਮਨੁੱਖੀ ਅਨੁਵਾਦ ਦੀ ਸਿਫਾਰਸ਼ ਕੀਤੀ ਜਾਂਦੀ ਹੈ। ਇਸ ਅਨੁਵਾਦ ਦੀ ਵਰਤੋਂ ਤੋਂ ਪੈਦਾ ਹੋਣ ਵਾਲੇ ਕਿਸੇ ਵੀ ਗਲਤਫਹਿਮੀ ਜਾਂ ਗਲਤ ਵਿਆਖਿਆ ਲਈ ਅਸੀਂ ਜ਼ਿੰਮੇਵਾਰ ਨਹੀਂ ਹਾਂ।
